# Binary Search Trees

In [2]:
class TreeNode:
    def __init__(self, key, val, left=None, right=None, parent=None):
        self.key = key
        self.payload = val
        self.left_child = left
        self.right_child= right
        self.parent = parent
        
    def __iter__(self):
        if self:
            if self.has_left_child():
                for elem in self.left_child:
                    yield elem
                    
            yield self.key
            
            if self.has_right_child():
                for elem in self.right_child:
                    yield elem
                    
    def has_left_child(self):
        return self.left_child
    
    def has_right_child(self):
        return self.right_child
    
    def is_left_child(self):
        return self.parent and self.parent.left_child is self
    
    def is_right_child(self):
        return self.parent and self.parent.right_child is self
    
    def is_root(self):
        return not self.parent
    
    def is_leaf(self):
        return not self.left_child and not self.right_child
    
    def has_any_children(self):
        return self.right_child or self.left_child
    
    def has_both_children(self):
        return self.right_child and self.left_child
    
    def replace_node_data(self, key, value, lc, rc):
        self.key = key
        self.payload = value
        self.left_child = lc
        self.right_child = rc
        
        if self.has_left_child():
            self.left_child.parent = self
            
        if self.has_right_child():
            self.right_child.parent = self
            
    def splice_out(self):
        if self.is_leaf():
            if self.is_left_child():
                self.parent.left_child = None
            else:
                self.parent.right_child = None
        elif self.has_any_children():
            if self.has_left_child():
                if self.is_left_child():
                    self.parent.left_child = self.left_child
                else:
                    self.parent.right_child = self.left_child
                    
                self.left_child.parent = self.parent
            else:  # has a right child
                if self.is_left_child():
                    self.parent.left_child = self.right_child
                else:
                    self.parent.right_child = self.right_child
                    
                self.right_child.parent = self.parent
                
    def find_successor(self):
        succ = None
        
        if self.has_right_child():
            succ = self.right_child.find_min()
        else:  # no right child? Then we work on left child
            if self.parent:  # it is an intermediate node
                if self.is_left_child():
                    succ = self.parent
                else:  # is a right child
                    self.parent.right_child = None
                    succ = self.parent.find_successor()
                    self.parent.right_child = self
        return succ
    
    
    def find_min(self):
        current = self
        
        while current.has_left_child():
            current = current.left_child

        return current

In [4]:
class BinarySearchTree:
    def __init__(self):
        self.root = None
        self.size = 0
    
    def __len__(self):
        return self.length()
    
    def __iter__(self):
        return self.root.__iter__()
    
    def __setitem__(self, k, v):
        self.put(k, v)
  
    def __getitem__(self, k):
        return self.get(k)
    
    def __contains__(self, k):
        #if self._get(key, self.root):
        #    return True
        #else:
        #    return False
        
        return self._get(k, self.root) is not None

    def __delitem__(self, k):
        self.delete(k)
    
    def length(self):
        return self.size
    
    def put(self, key, val):
        if self.root:
            self._put(key, val, self.root)
        else:  # the tree is non-existient
            self.root = TreeNode(key, val)
            
        self.size += 1
        
    def _put(self, key, val, current_node):
        if key < current_node.key:
            if current_node.has_left_child():
                self._put(key, val, current_node.left_child)
            else:
                current_node.left_child = TreeNode(key, val, parent=current_node)
        else:
            if current_node.has_right_child():
                self._put(key, val, current_node.right_child)
            else:
                current_node.right_child = TreeNode(key, val, parent=current_node)
                
    def get(self, key):
        if self.root:
            res = self._get(key, self.root)
            if res:
                # return the value of our TreeNode with matching key
                return res.payload
            else:
                return None
        else:
            return None
        
    def _get(self, key, current_node):
        if not current_node:
            return None
        elif current_node.key == key:
            return current_node
        elif key < current_node.key:
            return self._get(key, current_node.left_child)
        else:
            return self._get(key, current_node.right_child)
        
    def delete(self, key):
        if self.size > 1:
            node_to_remove = self._get(key, self.root)
            if node_to_remove:
                self.remove(node_to_remove)
                self.size -= 1
            else:
                raise KeyError("Key not found in tree!")
        elif self.size == 1 and self.root.key == key:
            # tree is completely removed, since it was only one node
            self.root = None
            self.size -= 1
        else:
            raise KeyError("Key not found in tree!")
            
    def remove(self, current_node):
        if current_node.is_leaf():  # leaf
            #if current_node == current_node.parent.left_child:
            if current_node.is_left_child():   
                current_node.parent.left_child = None
            else:
                current_node.parent.right_child = None
        elif current_node.has_both_children():  # interior or root
            succ = current_node.find_successor()
            succ.splice_out()
            current_node.key = succ.key
            current_node.payload = succ.payload
        else:  # node has one child
            if current_node.has_left_child():
                if current_node.is_left_child():
                    current_node.left_child.parent = current_node.parent
                    current_node.parent.left_child = current_node.left_child
                elif current_node.is_right_child():
                    current_node.left_child.parent = current_node.parent
                    current_node.parent.right_child = current_node.left_child
                else: #root
                    current_node.replace_node_data(current_node.left_child.key,
                                                   current_node.left_child.payload,
                                                   current_node.left_child.left_child,
                                                   current_node.left_child.right_child)
            else: # have right child
                if current_node.is_left_child():
                    current_node.right_child.parent = current_node.parent
                    current_node.parent.left_child = current_node.right_child
                elif current_node.is_right_child():
                    current_node.right_child.parent = current_node.parent
                    current_node.parent.right_child = current_node.right_child
                else:
                    current_node.replace_node_data(current_node.right_child.key,
                                                   current_node.right_child.payload,
                                                   current_node.right_child.left_child,
                                                   current_node.right_child.right_child)   

# Testing Our Binary Search Tree

In [5]:
bt = BinarySearchTree()

In [6]:
bt

In [7]:
bt[24] = "apple"

In [8]:
bt[24]

'apple'

In [9]:
bt.get(24)

'apple'

In [10]:
24 in bt

True

In [11]:
42 in bt

False

In [12]:
bt.size

1

In [13]:
len(bt)

1

In [14]:
bt.root

In [15]:
del bt[24]

In [16]:
len(bt)

0

In [35]:
bt[42]

"Don't Panic!"

In [32]:
bt[42] = "Don't Panic!"

In [24]:
bt.delete(24)

KeyError: 'Key not found in tree!'

In [25]:
bt[24] = "Panic Don't!"

In [31]:
list(bt)

[24, 42, 42, 42, 42, 42, 42]

In [37]:
d = {42: "Don't Panic!", 24: "Panic Don't!"}

In [38]:
d[24]

"Panic Don't!"

In [39]:
bt[24]

"Panic Don't!"

In [40]:
d

{42: "Don't Panic!", 24: "Panic Don't!"}

In [41]:
bt

In [42]:
for k in bt:
    print(f"{k}: {bt[k]!r}")

24: "Panic Don't!"
42: "Don't Panic!"
42: "Don't Panic!"
42: "Don't Panic!"
42: "Don't Panic!"
42: "Don't Panic!"
42: "Don't Panic!"
42: "Don't Panic!"


## Testing with names and ranks

In [43]:
import requests
from random import shuffle

In [44]:
def get_names(url):
    req = requests.get(url)
    lines = req.text.split("\n")
    names = []
    
    for line in lines:
        data = line.split()
        if len(data) == 4:
            names.append( (data[0], data[3]) )
            
    return names

In [45]:
def main():
    names = get_names("https://www2.census.gov/topics/genealogy/1990surnames/dist.female.first")
    print(f"Extracted {len(names)} names")
    shuffle(names)
    
    name_tree = BinarySearchTree()
    
    for name, rank in names:
        name_tree[int(rank)] = name
        
    return name_tree

In [46]:
nt = main()

Extracted 4275 names


In [47]:
len(nt)

4275

In [48]:
nt[33]

'ANNA'

In [51]:
nt[1]

'MARY'

In [52]:
nt[4000]

'YURIKO'

In [53]:
nt[1000]

'CELINA'

## Visualizing our BST

In [54]:
from graphviz import Digraph

class Stack:
    def __init__(self):
         self.items = []

    def is_empty(self):
         return self.items == []

    def push(self, item):
        self.items.append(item)

    def pop(self):
         return self.items.pop()

    def peek(self):
         return self.items[-1]

    def size(self):
         return len(self.items)

In [55]:
def viz_tree(r):
    stack = Stack()
    g = Digraph(node_attr={'shape': 'record', 'height': '.1'})
    _id = 0
    
#    if isinstance(r, BinaryTree):
#        current_node = r
#    elif isinstance(r, BinarySearchTree):
#        current_node = r.root  # root is a TreeNode object!    
    current_node = r.root
    
    leftward = True
    current_root_num = 0

    while True:
        if current_node:
            stack.push((_id, current_node))
            
            if isinstance(current_node, TreeNode):
                g.node(f'node{_id}',
                   f'<f0>|<f1> {current_node.key}:{current_node.payload}|<f2> ')
            elif isinstance(current_node, AVLTreeNode):
                g.node(f'node{_id}',
                       f'<f0>|<f1> {current_node.key}:{current_node.payload} ({current_node.balance_factor})|<f2> ')

            if _id >= 1:
                g.edge(f'node{current_root_num}:f{0 if leftward else 2}',
                       f'node{_id}:f1')

            leftward = True
            current_node = current_node.left_child  # left
            current_root_num = _id
            _id += 1

        if current_node is None and not stack.is_empty():
            count, popped_node = stack.pop()
            if popped_node.right_child:
                current_root_num = count
                current_node = popped_node.right_child  # right
                leftward = False

        if current_node is None and stack.is_empty():
            break

    return g

In [56]:
g = viz_tree(nt)

In [57]:
g.render("bst")

'bst.pdf'

## Visualizing with 'names' as keys

In [ ]:
def main():
    names = get_names("https://www2.census.gov/topics/genealogy/1990surnames/dist.female.first")
    print(f"Extracted {len(names)} names")
    shuffle(names)
    
    name_tree = BinarySearchTree()
    
    for name, rank in names:
        name_tree[name] = int(rank)
        
    return name_tree

In [ ]:
nt = main()

In [ ]:
g = viz_tree(nt)

In [ ]:
g.render("bst_names_as_key")

## Visualizing with sorted 'names' as keys

In [ ]:
def main():
    names = get_names("https://www2.census.gov/topics/genealogy/1990surnames/dist.female.first")
    print(f"Extracted {len(names)} names")
    
    # No shuffling!
    #shuffle(names)
    
    # names[("MARY", "1"), ...)
    names.sort(key=lambda t: t[0])
    
    name_tree = BinarySearchTree()
    
    for name, rank in names:
        name_tree[name] = int(rank)
        
    return name_tree

In [ ]:
nt = main()

In [ ]:
g = viz_tree(nt)

In [ ]:
g.render("bst_names_as_key_sorted")

## Visualizing with sorted 'names' as keys, smaller subset

In [ ]:
def main():
    names = get_names("https://www2.census.gov/topics/genealogy/1990surnames/dist.female.first")
    print(f"Extracted {len(names)} names")
    
    # No shuffling!
    #shuffle(names)
    
    # names[("MARY", "1"), ...)
    names.sort(key=lambda t: t[0])
    
    name_tree = BinarySearchTree()
    
    for name, rank in names[:100]:  # limit our tree to 100 names!
        name_tree[name] = int(rank)
        
    return name_tree

In [ ]:
nt = main()

In [ ]:
g = viz_tree(nt)

In [ ]:
g.render("bst_names_as_key_sorted")